In [ ]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import LabelEncoder
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
!pip install catboost
from catboost import CatBoostClassifier
!pip install https://github.com/pandas-profiling/pandas-profiling/archive/master.zip
import pandas_profiling as pp

     |████████████████████████████████| 67.3MB 53kB/s 
     \ 38.4MB 565kB/s
     |████████████████████████████████| 81kB 4.1MB/s 
     |████████████████████████████████| 1.1MB 8.6MB/s 
     |████████████████████████████████| 3.2MB 24.9MB/s 
     |████████████████████████████████| 61kB 5.3MB/s 
     |████████████████████████████████| 81kB 7.5MB/s 
     |████████████████████████████████| 296kB 51.9MB/s 
  Created wheel for pandas-profiling: filename=pandas_profiling-2.12.0-py2.py3-none-any.whl size=243829 sha256=54e1f9fbfcec011f1cf28eee890f161a80a8b433c41403d9dc325919e9d70029
  Stored in directory: /tmp/pip-ephem-wheel-cache-k1ek77gb/wheels/56/c2/dd/8d945b0443c35df7d5f62fa9e9ae105a2d8b286302b92e0109
  Created wheel for htmlmin: filename=htmlmin-0.1.12-cp37-none-any.whl size=27085 sha256=df7d1cd4a2eb972cfdb866bb90407b2a77934733da3960c5f61f0e9148992912
  Stored in directory: /root/.cache/pip/wheels/43/07/ac/7c5a9d708d65247ac1f94066cf1db075540b85716c30255459
  Created wheel for phik: filen

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!cp -r --recursive  "/content/drive/MyDrive/DataScienceCompetitions/ChurnRiskRate_prediction/test.csv" "/content"
!cp -r --recursive  "/content/drive/MyDrive/DataScienceCompetitions/ChurnRiskRate_prediction/train.csv" "/content"
!cp -r --recursive  "/content/drive/MyDrive/DataScienceCompetitions/ChurnRiskRate_prediction/sample_submission.csv" "/content"

In [ ]:
df_train = pd.read_csv("train.csv")
df_train["region_category"] =       df_train["region_category"].fillna("Town")
df_train["preferred_offer_types"] = df_train["preferred_offer_types"].fillna("Gift Vouchers/Coupons")
df_train["points_in_wallet"] =      df_train["points_in_wallet"].fillna(df_train.points_in_wallet.mean())
df_train["train"] = 1
print(df_train.shape)
df_train.head()

(36992, 26)


customer_id  ... train
0      fffe4300490044003600300030003800  ...     1
1  fffe43004900440032003100300035003700  ...     1
2      fffe4300490044003100390032003600  ...     1
3  fffe43004900440036003000330031003600  ...     1
4  fffe43004900440031003900350030003600  ...     1

[5 rows x 26 columns]

In [ ]:
profile = pp.ProfileReport(train, title='Pandas Profiling Report', explorative=True)
profile.to_file("profile.html")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/43 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
# ct = 0
# for i in df_train["joined_through_referral"]:
#     if i=="?":
#         print(df_train["medium_of_operation"][ct],df_train["joined_through_referral"][ct])
#     ct=ct+1


In [ ]:
# cou = 0
# neg = []
# for i in  df["avg_frequency_login_days"]:
#     if i == "Error":
#         continue
#     if int(float(i))<0:
#         cou = cou+1
#         neg.append(int(float(i)))
# cou, max(neg), min(neg)

(1034, -1, -46)

In [ ]:
df_test = pd.read_csv("test.csv")
df_test["region_category"] =       df_test["region_category"].fillna("Town")
df_test["preferred_offer_types"] = df_test["preferred_offer_types"].fillna("Gift Vouchers/Coupons")
df_test["points_in_wallet"] =      df_test["points_in_wallet"].fillna(df_train.points_in_wallet.mean())
df_test["train"] = 0
print(df_test.shape)
df_test.head()

(19919, 25)


customer_id  ... train
0  fffe43004900440031003700300030003400  ...     0
1  fffe43004900440031003900370037003300  ...     0
2  fffe43004900440034003800360037003000  ...     0
3  fffe43004900440036003200370033003400  ...     0
4  fffe43004900440035003000370031003900  ...     0

[5 rows x 25 columns]

In [ ]:
df = pd.concat([df_train,df_test])
df = df.sample(frac=1)
print(df.shape)
df.head()

(56911, 26)


customer_id  ... train
11829  fffe43004900440034003400340037003100  ...     0
7606   fffe43004900440032003100300038003600  ...     1
11049  fffe43004900440034003900300030003800  ...     0
11182  fffe43004900440036003000360033003900  ...     0
17419  fffe43004900440034003000320037003600  ...     1

[5 rows x 26 columns]

In [ ]:
# pp = df_train[df_train['churn_risk_score']==-1].index
# df_train = df_train.drop(pp)
# print(df_train.shape)

df["churn_risk_score"] = df["churn_risk_score"].replace(-1, 1)


df["days_since_last_login"] = df["days_since_last_login"].replace(-999, 0)

In [ ]:
for i in df_train.columns:
    print(i, "       ",df_train[i].nunique())

customer_id         36992
Name         36992
age         55
gender         3
security_no         36992
region_category         3
membership_category         6
joining_date         1096
joined_through_referral         3
referral_id         11359
preferred_offer_types         3
medium_of_operation         4
internet_option         3
last_visit_time         30101
days_since_last_login         27
avg_time_spent         25961
avg_transaction_value         36894
avg_frequency_login_days         1654
points_in_wallet         23700
used_special_discount         2
offer_application_preference         2
past_complaint         2
complaint_status         5
feedback         9
churn_risk_score         5
train         1


In [ ]:
for i in df_test.columns:
    print(i, "       ",df_test[i].nunique())

customer_id         19919
Name         19919
age         55
gender         3
security_no         19919
region_category         3
membership_category         6
joining_date         1096
joined_through_referral         3
referral_id         7603
preferred_offer_types         3
medium_of_operation         4
internet_option         3
last_visit_time         17821
days_since_last_login         27
avg_time_spent         15703
avg_transaction_value         19883
avg_frequency_login_days         946
points_in_wallet         14582
used_special_discount         2
offer_application_preference         2
past_complaint         2
complaint_status         5
feedback         9
train         1


In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 56911 entries, 3113 to 3112
Data columns (total 28 columns):
 #   Column                        Non-Null Count  Dtype         
---  ------                        --------------  -----         
 0   customer_id                   56911 non-null  object        
 1   Name                          56911 non-null  object        
 2   age                           56911 non-null  int64         
 3   gender                        56911 non-null  int64         
 4   security_no                   56911 non-null  object        
 5   region_category               56911 non-null  int64         
 6   membership_category           56911 non-null  int64         
 7   joining_date                  56911 non-null  object        
 8   joined_through_referral       56911 non-null  int64         
 9   referral_id                   56911 non-null  object        
 10  preferred_offer_types         56911 non-null  int64         
 11  medium_of_operation       

In [ ]:
le = LabelEncoder()
df["gender"] = le.fit_transform(df["gender"])

le = LabelEncoder()
df["region_category"] = le.fit_transform(df["region_category"])

le = LabelEncoder()
df["membership_category"] = le.fit_transform(df["membership_category"])

le = LabelEncoder()
df["joined_through_referral"] = le.fit_transform(df["joined_through_referral"])

le = LabelEncoder()
df["preferred_offer_types"] = le.fit_transform(df["preferred_offer_types"])

le = LabelEncoder()
df["medium_of_operation"] = le.fit_transform(df["medium_of_operation"])

le = LabelEncoder()
df["internet_option"] = le.fit_transform(df["internet_option"])

le = LabelEncoder()
df["used_special_discount"] = le.fit_transform(df["used_special_discount"])

le = LabelEncoder()
df["offer_application_preference"] = le.fit_transform(df["offer_application_preference"])

le = LabelEncoder()
df["past_complaint"] = le.fit_transform(df["past_complaint"])

le = LabelEncoder()
df["complaint_status"] = le.fit_transform(df["complaint_status"])

le = LabelEncoder()
df["feedback"] = le.fit_transform(df["feedback"])







print(df.shape)
df.head()

(56911, 26)


customer_id  ... train
11829  fffe43004900440034003400340037003100  ...     0
7606   fffe43004900440032003100300038003600  ...     1
11049  fffe43004900440034003900300030003800  ...     0
11182  fffe43004900440036003000360033003900  ...     0
17419  fffe43004900440034003000320037003600  ...     1

[5 rows x 26 columns]

In [ ]:
df["PCgroupCS"] = df.groupby(["past_complaint","complaint_status"]).ngroup().astype('int')
print(df.shape)
df.head()

(56911, 31)


customer_id                Name  ...  day  PCgroupCS
34696  fffe43004900440031003500320032003000           Elke Near  ...    2          0
17041  fffe43004900440033003000300033003000     Stella Heineman  ...   30          0
11150  fffe43004900440031003300340036003600      Dorine Leitner  ...   17          0
7674   fffe43004900440033003900360037003500  Kristeen Scroggins  ...    1          0
30513  fffe43004900440032003600390038003600       Rebecka Ragin  ...    3          0

[5 rows x 31 columns]

In [ ]:
df["datee"] = pd.to_datetime(df['joining_date'])
print(df.shape)
df.head()

(56911, 27)


customer_id              Name  ...  train      datee
11829  fffe43004900440034003400340037003100       Perry Oatis  ...      0 2015-03-01
7606   fffe43004900440032003100300038003600   Earlie Cardwell  ...      1 2017-10-08
11049  fffe43004900440034003900300030003800    Lesia Gonzalas  ...      0 2016-04-02
11182  fffe43004900440036003000360033003900    Donya Tijerina  ...      0 2017-09-20
17419  fffe43004900440034003000320037003600  Chantel Finnerty  ...      1 2017-07-21

[5 rows x 27 columns]

In [ ]:
df["mon"] = df["datee"].dt.month
df["yr"] = df["datee"].dt.year
df["day"] = df["datee"].dt.day
print(df.shape)
df.head()

(56911, 30)


customer_id              Name  ...    yr  day
11829  fffe43004900440034003400340037003100       Perry Oatis  ...  2015    1
7606   fffe43004900440032003100300038003600   Earlie Cardwell  ...  2017    8
11049  fffe43004900440034003900300030003800    Lesia Gonzalas  ...  2016    2
11182  fffe43004900440036003000360033003900    Donya Tijerina  ...  2017   20
17419  fffe43004900440034003000320037003600  Chantel Finnerty  ...  2017   21

[5 rows x 30 columns]

In [142]:
df = df.sample(frac=1)

train = df[df["train"]==1]
train = train.reset_index(drop=True)
print(train.shape)

test = df[df["train"]==0]
test = test.reset_index(drop=True)
print(test.shape)

test.head()

(36992, 31)
(19919, 31)


customer_id            Name  ...  day  PCgroupCS
0  fffe43004900440031003300340037003500  Joseph Jarrard  ...   22          0
1  fffe43004900440035003900370039003900   Selena Freund  ...    5          4
2  fffe43004900440035003500300038003300      Guy Lufkin  ...   30          0
3  fffe43004900440031003300330033003600    Melita Oatis  ...   19          1
4  fffe43004900440036003100340034003900     Nelda Taube  ...   27          0

[5 rows x 31 columns]

In [162]:
ay1 = train["customer_id"].tolist()

ay2 = test["customer_id"].tolist()

ay3 = ay1 + ay2

len(ay1), len(ay2), len(ay3),  len(set(ay1)), len(set(ay2)), len(set(ay3))

(36992, 19919, 56911, 36992, 19919, 56911)

In [144]:
def training(X, Y):
    # model = XGBClassifier(n_estimators=100 , max_depth=8, verbose=0)
    # model = LGBMClassifier(max_depth=30 , n_estimators=500 , num_leaves=31)
    model = CatBoostClassifier(n_estimators=800, depth=5, verbose=0)
    model.fit(X, Y)
    return model


def testing(X):
    ans = model.predict(X)
    return ans



In [145]:

col_to_drop = ["train", "churn_risk_score", "customer_id", "Name", "security_no", "joining_date", "referral_id", "last_visit_time", "avg_frequency_login_days", "datee", "mon", "day", "yr", "PCgroupCS"]
trainX = train.drop(col_to_drop, axis=1)
print(trainX.columns)
print(trainX.shape)


trainY = train["churn_risk_score"]
print(trainY.shape)

model = training(trainX, trainY)


Index(['age', 'gender', 'region_category', 'membership_category',
       'joined_through_referral', 'preferred_offer_types',
       'medium_of_operation', 'internet_option', 'days_since_last_login',
       'avg_time_spent', 'avg_transaction_value', 'points_in_wallet',
       'used_special_discount', 'offer_application_preference',
       'past_complaint', 'complaint_status', 'feedback'],
      dtype='object')
(36992, 17)
(36992,)


In [146]:
testX = test.drop(col_to_drop, axis=1)
print(testX.shape)
ans = testing(testX)
print(ans.shape)

(19919, 17)
(19919, 1)


In [147]:
#catboost


sample_sub = pd.read_csv("sample_submission.csv")
arr1 = []
arr2 = []

for ind in range(len(test)):
    j = test["customer_id"][ind]
    arr1.append(j)
    arr2.append(ans[ind][0])

print(len(arr1), len(arr2))

dic = {"customer_id": arr1, "churn_risk_score":arr2}
df_fin = pd.DataFrame(dic)

filename = "sub.csv"

df_fin.to_csv(filename , index=False)
from google.colab import files
files.download(filename)

19919 19919


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
#xgb


sample_sub = pd.read_csv("sample_submission.csv")
arr1 = []
arr2 = []

for ind in range(len(test)):
    j = test["customer_id"][ind]
    arr1.append(j)
    arr2.append(ans[ind])

print(len(arr1), len(arr2))

dic = {"customer_id": arr1, "churn_risk_score":arr2}
df_fin = pd.DataFrame(dic)

filename = "sub.csv"

df_fin.to_csv(filename , index=False)
from google.colab import files
files.download(filename)

In [ ]:
LGBMClassifier(max_depth=30 , n_estimators=500 , num_leaves=31)
75.63

model = XGBClassifier(n_estimators=100 , max_depth=8, verbose=0)
76.50

model = CatBoostClassifier(n_estimators=800, depth=5, verbose=0)
76.69

model = CatBoostClassifier(n_estimators=800, depth=7, verbose=0)
75.94

model = CatBoostClassifier(n_estimators=600, depth=5, verbose=0)
75.76

model = CatBoostClassifier(n_estimators=1000, depth=5, verbose=0)
76.13


wwithout feeback  67
with past_compliant  76.33
without complaint_status  76.10118